# Car ride-share potential in mid-size U.S. cities from geographic spread

This notebook supports the IBM Data Science Specialization on Coursera, per official report PDF. For all details, see the PDF

## Extract geographic location of mid-size U.S. cities

The 2017 U.S. census estimate for city size can be obtained from https://factfinder.census.gov/faces/tableservices/jsf/pages/productview.xhtml?src=bkmk . It is faithfully represented in a corresponding Wikipedia page https://en.wikipedia.org/w/index.php?title=List_of_United_States_cities_by_population&oldid=883568308 (retrieved 3 March 2019) from which it can be easily parsed.

In [1]:
import pandas as pd
import numpy as np

Following https://medium.com/analytics-vidhya/web-scraping-wiki-tables-using-beautifulsoup-and-python-6b9ea26d8722 (retrieved 24 Feb 2019) using BeautifulSoup to get a parseable representation of the Wikipedia page, then load the table with all cities into `city_table`:

In [2]:
import requests
url = 'https://en.wikipedia.org/w/index.php?title=List_of_United_States_cities_by_population&oldid=883568308'
website_url = requests.get(url).text

from bs4 import BeautifulSoup
soup = BeautifulSoup(website_url, 'lxml')
city_table = soup.find('table', { 'class' : 'wikitable sortable' })
print("{}\n\n   [...]\n\n{}".format(str(city_table)[:500].replace('\n', '').replace('<tr>', '\n\n<tr>'), str(city_table)[-500:]))

<table class="wikitable sortable" style="text-align:center"><tbody>

<tr><th>2017<br/>rank</th><th>City</th><th>State<sup class="reference" id="cite_ref-5"><a href="#cite_note-5">[5]</a></sup></th><th>2017<br/>estimate</th><th>2010<br/>Census</th><th>Change</th><th colspan="2">2016 land area</th><th colspan="2">2016 population density</th><th>Location</th></tr>

<tr><td>1</td><td style="text-align:left;background-color:#cfecec"><i><a href="/wiki/New_York_City" title="New York 

   [...]

"latitude">38°21′14″N</span> <span class="longitude">121°58′22″W</span></span></span><span class="geo-multi-punct">﻿ / ﻿</span><span class="geo-default"><span class="vcard"><span class="geo-dec" title="Maps, aerial photos, and other data for this location">38.3539°N 121.9728°W</span><span style="display:none">﻿ / <span class="geo">38.3539; -121.9728</span></span><span style="display:none">﻿ (<span class="fn org">Vacaville</span>)</span></span></span></a></span></small>
</td></tr></tbody></table>


From `city_table` find all cities with an estimated 2017 population between 300,000 and 400,000 and parse out the latitude and longitude into numeric values:
* City name is the second column (remove references in square brackets if present),
* city state is the third column,
* population is the 4th column (remove thousands-separator commas before interpreting as integer),
* lattitude and longitude is contained in the 11th column, but has to be substring-filtered.

In [3]:
import re

l = []

table_rows = city_table.find_all('tr')
for tr in table_rows:
    td = tr.find_all('td')
    row = [tr.text.strip() for tr in td]
    if len(row) < 1:
        print("(ignoring empty row)")
        test_size = 0
    else:
        test_size = int(row[3].replace(',', ''))
        
    if test_size >= 300000 and test_size <= 400000:
        city_name = re.sub('\[.*\]', '', row[1])
        city_state = row[2]
        city_estd_pop2017 = test_size
        city_latlongraw = re.sub('^.*/', '', re.sub('\(.*\)', '', row[10])).replace(' ', '')
        # strip non-ASCII residue
        city_latlongraw = city_latlongraw.encode('ascii',errors='ignore').decode()
        city_lat = float(re.sub(';.*$', '', city_latlongraw))
        city_long = float(re.sub('^.*;', '', city_latlongraw))
        l.append([city_name, city_state, city_estd_pop2017, city_lat, city_long])

cities_df = pd.DataFrame(l)
cities_df.columns = ['City name', 'City state', 'Population', 'Latitude', 'Longitude']
print(cities_df)

(ignoring empty row)
         City name    City state  Population  Latitude  Longitude
0        Arlington         Texas      396394   32.7007   -97.1247
1      New Orleans     Louisiana      393292   30.0534   -89.9345
2          Wichita        Kansas      390591   37.6907   -97.3459
3        Cleveland          Ohio      385525   41.4785   -81.6794
4            Tampa       Florida      385430   27.9701   -82.4797
5      Bakersfield    California      380874   35.3212  -119.0183
6           Aurora      Colorado      366623   39.6880  -104.6897
7          Anaheim    California      352497   33.8555  -117.7601
8         Honolulu        Hawaii      350395   21.3243  -157.8476
9        Santa Ana    California      334136   33.7363  -117.8830
10       Riverside    California      327728   33.9381  -117.3932
11  Corpus Christi         Texas      325605   27.7543   -97.1734
12       Lexington      Kentucky      321959   38.0407   -84.4583
13        Stockton    California      310496   37.9763 

In [4]:
# persist the DataFrame (at least for a little while)
cities_df.to_csv('cities_df.csv')

## Get venues using Foursquare

<!--
CLIENT_ID = 'NBLOR5JJCSM43LTXYWBQYVJ5U3LMNZ2ULCHERZAZVLJTHBYA' # your Foursquare ID
CLIENT_SECRET = 'D1G4RELNK2MGSOZSO1C4DTGPYBAWHIW0MQJTXWSBTGH2JL41' # your Foursquare Secret
-->

In [7]:

print('CLIENT_ID set: {}'.format(CLIENT_ID is not None))
print('CLIENT_SECRET set: {}'.format(CLIENT_SECRET is not None))

VERSION = '20180605' # Foursquare API version

CLIENT_ID set: True
CLIENT_SECRET set: True


In [8]:
# (optional: restore all of the above data from storaget, import all libraries from above)
import pandas as pd
import numpy as np
import requests
import re

cities_df = pd.read_csv('cities_df.csv')

Define a Foursquare query that gets all venues within a default radius of 500 meters around a latitude and longitude. The number of venues returned is capped at 100 by default.

In [94]:
def getVenuesNearLatLong(latitude, longitude, radius=500, limit=100, verbose=True):
    
    venues_list=[]
                
    # create the API request URL
    url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION,
            latitude, 
            longitude, 
            radius, 
            limit)
            
    # make the GET request
    results_raw = requests.get(url)
    try:
        results = results_raw.json()["response"]['groups'][0]['items']
    except:
        print('(err)', end='')
        results = [{}]
        
    # return only relevant information for each nearby venue
    venues_list.append([(
            latitude, 
            longitude, 
            v['venue']['name'], 
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    if (len(results) > 0):
        nearby_venues.columns = [
                  'Latitude', 
                  'Longitude', 
                  'Venue', 
                  'Venue Category']
    
    if verbose:
        print('found {} venues within {} meters of {}/{}'.format(len(results), radius, latitude, longitude))
    else:
        print('{}'.format(len(results)), end='. ')
    
    return(nearby_venues)

### Test number of venues finder

Using the first record in the cities_df DataFrame, test the function defined above.

In [95]:
print(cities_df.head(1))

   Unnamed: 0  City name City state  Population  Latitude  Longitude
0           0  Arlington      Texas      396394   32.7007   -97.1247


In [96]:
venues_df = getVenuesNearLatLong(cities_df.Latitude[0], cities_df.Longitude[0])
city_name = cities_df['City name'][0]
city_state = cities_df['City state'][0]

found 8 venues within 500 meters of 32.7007/-97.1247


In [97]:
print('{}, {} venues_df.shape = {}'.format(city_name, city_state, venues_df.shape))
venues_df

Arlington, Texas venues_df.shape = (8, 4)


Latitude  Longitude                    Venue           Venue Category
0   32.7007   -97.1247   Krispy Kreme Doughnuts               Donut Shop
1   32.7007   -97.1247        Texas Vision Care             Optical Shop
2   32.7007   -97.1247  Kenner's Kolache Bakery           Breakfast Spot
3   32.7007   -97.1247         Cooper St Bakery                   Bakery
4   32.7007   -97.1247           El Pollo Regio       Mexican Restaurant
5   32.7007   -97.1247          Avis Car Rental      Rental Car Location
6   32.7007   -97.1247       Euro Image Med Spa  Health & Beauty Service
7   32.7007   -97.1247               Metro Flex                      Gym

### Search hex grid around a given coordinate

Define a function that takes a latitude and longitude and return the venues at 6 coordinate points around that location, in a hex grid. Each point in the hex grid will be labeled by an integer as shown in the following diagram around the origin (0,0):

```
        ( -1, 1 )      ( 0, 1 )
                \      /
                 \    /
( -1, 0 )  ---  ( 0, 0 )  ---  ( 1, 0 )
                  /  \
                 /    \
        ( 0, -1 )     ( 1, -1 )
```

Given a latitude and longitude, the entire hex grid can therefore be described by a set of tuples `( x, y )`. The function will collect the venues result and append it to a dictionary that is keyed by these `( x, y )` tuples.

In [50]:
import math

def get_venues_in_hex_grid(latitude, longitude, venues_dict, this_coord, radius=500, limit=100, new_coords=[], verbose=True):
    '''
    Calls Foursquare in a hex grid around a given coordinate point. If venues
    have already been searched on one of the hex grid points, that result is
    kept and no new search is executed.
    
    Parameters:
    
    latitude and longitude are as of the origin coordinate (0, 0),
    venues_dict are the venues found so far (dictionary keys are a coordinate tuple),
    this_coord is the center coordinate around which the hex grid is to be searched,
    radius is the radius [meters] to search around a coordinate point,
    limit is the maximum number of venues to return from a Foursquare search.
    new_coords is a list of coordinate points that wasn't probed yet
    
    Returns a list of new coordinate tuples appended to the new_coords parameter, if any
    '''
    
    r_earth = 6378000. # approximate radius of the Earth in meters
    pi = math.pi
    sqrt_three = math.sqrt(3.)
    overlap = 1.4 # 40% overlap
    
    cx = this_coord[0] # center X
    cy = this_coord[1] # center Y
    hex_coords = [ (cx-1,cy), (cx+1, cy), (cx,cy-1), (cx,cy+1), (cx-1,cy+1), (cx+1,cy-1) ] # the gex grid around this_coord
    
    if (cx, cy) in new_coords:
        new_coords.remove((cx, cy))
    
    for this_hex in hex_coords:
        if not this_hex in venues_dict:
            # the coordinate has not been searched for
            
            # get the x- and y-step from a hex grid; start with a square grid (letting the circles overlap a bit):
            dx_square = this_hex[0] * radius * ( overlap / 2. )
            dy_square = this_hex[1] * radius * ( overlap / 2. )
            # now convert to a hex grid:
            dx = dx_square + dy_square / 2.
            dy = dy_square * ( sqrt_three / 2. )
            # approximate the center point's latitude and longitude assuming locally flat Earth
            hex_latitude  = latitude  + (dy / r_earth) * (180 / pi);
            hex_longitude = longitude + (dx / r_earth) * (180 / pi) / math.cos(latitude * pi/180);
            
            if verbose:
                print('getting coordinate {}...'.format(this_hex))
            else:
                print('({},{}):'.format(this_hex[0], this_hex[1]), end='')
                
            this_venues = getVenuesNearLatLong(hex_latitude, hex_longitude, radius=radius, limit=limit, verbose=verbose)
            venues_dict[this_hex] = this_venues
            if not this_hex in new_coords:
                new_coords.append(this_hex)
    
    return new_coords


Test the hexagonal grid function on the above city, to see how it functions.

In [98]:
# initialize venues_dict with the venues dataframe at the origin
venues_dict = {}
origin_coord = (0,0)
venues_dict[origin_coord] = venues_df
lat_orig = cities_df.Latitude[0]
long_orig = cities_df.Longitude[0]

# call the hex grid exploration function
new_coords = get_venues_in_hex_grid(lat_orig, long_orig, venues_dict, (0,0) )


print('\n ... same call but with terse output:\n')

venues_dict = {}
origin_coord = (0,0)
venues_dict[origin_coord] = venues_df
new_coords = get_venues_in_hex_grid(lat_orig, long_orig, venues_dict, (0,0), verbose=False )

getting coordinate (-1, 0)...
found 3 venues within 500 meters of 32.7007/-97.12843637006064
getting coordinate (1, 0)...
found 7 venues within 500 meters of 32.7007/-97.12096362993937
getting coordinate (0, -1)...
found 12 venues within 500 meters of 32.69797706801414/-97.12656818503032
getting coordinate (0, 1)...
found 10 venues within 500 meters of 32.703422931985855/-97.12283181496969
getting coordinate (-1, 1)...
found 5 venues within 500 meters of 32.703422931985855/-97.12656818503032
getting coordinate (1, -1)...
found 12 venues within 500 meters of 32.69797706801414/-97.12283181496969

 ... same call but with terse output:

(-1,0):3. (1,0):7. (0,-1):12. (0,1):10. (-1,1):5. (1,-1):12. 

Output the result:

In [99]:
print('New coordinates probed: {}\n'.format(new_coords))

for key, entry in venues_dict.items():
    print('Venues at {}:\n{}\n\n'.format(key, entry['Venue Category'])) 

New coordinates probed: [(-5, -4), (-4, -5), (-5, -3), (-3, -5), (-4, -4), (-5, -2), (-5, -1), (-5, 0), (-5, 1), (-5, 2), (-5, 3), (-5, 4), (-4, 5), (-5, 5), (-2, -5), (-3, 5), (-1, -5), (-2, 5), (0, -5), (-1, 5), (1, -5), (0, 5), (2, -5), (1, 5), (3, -5), (2, 5), (4, -5), (3, 5), (5, -4), (5, -5), (5, -3), (5, -2), (5, -1), (5, 0), (5, 1), (5, 2), (5, 3), (5, 4), (4, 5), (-1, 0), (1, 0), (0, -1), (0, 1), (-1, 1), (1, -1)]

Venues at (0, 1):
0                Donut Shop
1      Caribbean Restaurant
2              Burger Joint
3        Mexican Restaurant
4              Burger Joint
5       Filipino Restaurant
6    Thrift / Vintage Store
7               Pizza Place
8        Mexican Restaurant
9        Mexican Restaurant
Name: Venue Category, dtype: object


Venues at (-1, 1):
0              Dessert Shop
1        Mexican Restaurant
2        Mexican Restaurant
3    Thrift / Vintage Store
4               Pizza Place
Name: Venue Category, dtype: object


Venues at (0, 0):
0                 Don

Get a graphical representation of where these venues are, using folium

In [16]:
# import libraries required for folium

import json
!conda install -c conda-forge geopy --yes
from geopy.geocoders import Nominatim
from pandas.io.json import json_normalize
import matplotlib.cm as cm
import matplotlib.colors as colors
!conda install -c conda-forge folium=0.5.0 --yes
import folium

Fetching package metadata .............
Solving package specifications: .

Package plan for installation in environment /opt/conda/envs/DSX-Python35:

The following NEW packages will be INSTALLED:

    geographiclib: 1.49-py_0   conda-forge
    geopy:         1.18.1-py_0 conda-forge

geographiclib- 100% |################################| Time: 0:00:00  23.38 MB/s
geopy-1.18.1-p 100% |################################| Time: 0:00:00  36.90 MB/s
Fetching package metadata .............
Solving package specifications: .

Package plan for installation in environment /opt/conda/envs/DSX-Python35:

The following NEW packages will be INSTALLED:

    altair:  2.2.2-py35_1 conda-forge
    branca:  0.3.1-py_0   conda-forge
    folium:  0.5.0-py_0   conda-forge
    vincent: 0.4.4-py_1   conda-forge

altair-2.2.2-p 100% |################################| Time: 0:00:00  53.28 MB/s
branca-0.3.1-p 100% |################################| Time: 0:00:00  35.31 MB/s
vincent-0.4.4- 100% |###################

In [100]:
def make_map_from_dict(lat_orig, long_orig, venues_dict, zoom_start, city_name='(city_name)', city_state='(city_state)', radius_zoom=1.0):
    new_map = folium.Map(location=[lat_orig, long_orig], zoom_start=zoom_start)

    # add markers to map
    for coords, venues in venues_dict.items():
        if venues.shape[0] > 0: 
            label = '{}, # venues: {}'.format(coords, venues.shape[0])
            label = folium.Popup(label, parse_html=True)
            folium.CircleMarker(
                [venues['Latitude'][0], venues['Longitude'][0]],
                radius=venues.shape[0] * radius_zoom,
                popup=label,
                color='blue',
                fill=True,
                fill_color='#3186cc',
                fill_opacity=0.7,
                parse_html=False).add_to(new_map)
        
    legend_html = ('<div style="position: fixed; top: 30px; right: 50px; width: 450px;' 
                + 'height: 30px; border: 2px solid grey; z-index: 9999; font-size: 16px; background-color: white">' 
                + '&nbsp;{},&nbsp;{}' 
                + '</div>').format(
                     city_name,
                     city_state
                     )
    new_map.get_root().html.add_child(folium.Element(legend_html))
     
    return new_map

make_map_from_dict(lat_orig, long_orig, venues_dict, 14, city_name, city_state)

### Interpretation of the test

A quick visual inspection confirms the correctness of the algorithm (the coordinates and expected number of venues matches the text printout).

However, it is also obvious that the city is much larger, and many more venue points would have to be calculated this way. The sandbox account into Foursquare is limited to just under 1000 API queries per day, and we have 19 cities in our data set.

Performing 100 query points for each city amounts to 1900 Foursquare API queries. This can be done over the course of two or three days. 100 query points, however, is just a 10x10 grid. Therefore, increase the search size to 1500 meters, and accept that in certain circles we'll exceed the maximum number of venues returned by Foursquare.

Re-testing with the new parameters:

In [71]:
# initialize venues_dict with the venues dataframe at the origin
venues_dict = {}
origin_coord = (0,0)
lat_orig = cities_df.Latitude[0]
long_orig = cities_df.Longitude[0]
venues_dict[origin_coord] = getVenuesNearLatLong(lat_orig, long_orig, radius=1500)

# call the hex grid exploration function
new_coords = get_venues_in_hex_grid(lat_orig, long_orig, venues_dict, (0,0), radius=1500, verbose=False)

found 55 venues within 1500 meters of 32.7007/-97.1247
(-1,0):64. (1,0):69. (0,-1):93. (0,1):60. (-1,1):49. (1,-1):77. 

In [72]:
make_map_from_dict(lat_orig, long_orig, venues_dict, 14, city_name, city_state)

At the risk of hitting the maximum number of venues returned from Foursquare, the radius 1500 meters will be chosen going forward. The number of cities will be capped at 19, and the number of venue points in the algorithm at 100 so that we can gather all required data within 2-3 days from Foursquare.

In a real analysis, we would of course pay for a Foursquare subscription and get many more data points.

### Manually run the next iteration

The algorithm to be built will then look at the coordinate points found so far, pick the one with the highest number of venues, and perform a hex lookup around that coordinate. In the above city, the most venues were returned at coordinate `(0, -1)`. Manually perform an iteration step around that coordinate:

In [56]:
new_coords = get_venues_in_hex_grid(lat_orig, long_orig, venues_dict, (0,-1), radius=1500, new_coords=new_coords)

getting coordinate (-1, -1)...
found 46 venues within 1500 meters of 32.69253120404243/-97.14151366527287
getting coordinate (0, -2)...
found 100 venues within 1500 meters of 32.684362408084866/-97.13590911018191
getting coordinate (1, -2)...
found 93 venues within 1500 meters of 32.684362408084866/-97.1247


In [57]:
print('total new coordinates not probed yet: {}'.format(new_coords))

total new coordinates not probed yet: [(-1, 0), (1, 0), (0, 1), (-1, 1), (1, -1), (-1, -1), (0, -2), (1, -2)]


Three new coordinate points were queried from Foursquare, because the other three are already known. Resulting map:

In [58]:
make_map_from_dict(lat_orig, long_orig, venues_dict, 14, city_name, city_state)

Just to get an overview, perform a grid query for venues and plot the result.

In [59]:
for x in range(-4, 5):
    for y in range(-4, 5):
        get_venues_in_hex_grid(lat_orig, long_orig, venues_dict, (x,y), radius=1500, verbose=False)

(-5,-4):59. (-3,-4):17. (-4,-5):29. (-4,-3):52. (-5,-3):68. (-3,-5):15. (-3,-3):8. (-4,-4):66. (-4,-2):21. (-5,-2):48. (-3,-2):8. (-4,-1):8. (-5,-1):17. (-3,-1):8. (-4,0):13. (-5,0):14. (-3,0):36. (-4,1):32. (-5,1):21. (-3,1):61. (-4,2):80. (-5,2):19. (-3,2):88. (-4,3):45. (-5,3):39. (-3,3):54. (-4,4):50. (-5,4):37. (-3,4):31. (-4,5):47. (-5,5):26. (-2,-4):16. (-2,-5):11. (-2,-3):14. (-2,-2):13. (-2,-1):7. (-2,0):39. (-2,1):60. (-2,2):68. (-2,3):35. (-2,4):36. (-3,5):38. (-1,-4):24. (-1,-5):10. (-1,-3):33. (-1,-2):43. (-1,2):71. (-1,3):58. (-1,4):70. (-2,5):50. (0,-4):97. (0,-5):11. (0,-3):100. (0,2):71. (0,3):64. (0,4):54. (-1,5):75. (1,-4):100. (1,-5):94. (1,-3):100. (1,1):57. (1,2):79. (1,3):31. (1,4):44. (0,5):92. (2,-4):100. (2,-5):71. (2,-3):100. (2,-2):100. (2,-1):58. (2,0):46. (2,1):48. (2,2):57. (2,3):26. (2,4):28. (1,5):64. (3,-4):75. (3,-5):26. (3,-3):96. (3,-2):75. (3,-1):16. (3,0):54. (3,1):42. (3,2):42. (3,3):32. (3,4):16. (2,5):56. (4,-4):72. (4,-5):18. (4,-3):79. (4,-2)

That's one way of running up your Foursquare quota! Result:

In [60]:
make_map_from_dict(lat_orig, long_orig, venues_dict, 13, city_name, city_state, radius_zoom=0.25)

### Edge case test: no venues

In the middle of the ocean there are no venues, since we're in the Atlantic. Make sure it behaves OK in that edge case as well.

In [101]:
# initialize venues_dict with the venues dataframe at the origin
venues_dict = {}
origin_coord = (0,0)
venues_dict[origin_coord] = {}
lat_orig = -10
long_orig = 0

# call the hex grid exploration function
new_coords = get_venues_in_hex_grid(lat_orig, long_orig, venues_dict, (0,0) )

venues_dict

getting coordinate (-1, 0)...
found 0 venues within 500 meters of -10.0/-0.003192674936220234
getting coordinate (1, 0)...
found 0 venues within 500 meters of -10.0/0.003192674936220234
getting coordinate (0, -1)...
found 0 venues within 500 meters of -10.002722931985856/-0.001596337468110117
getting coordinate (0, 1)...
found 0 venues within 500 meters of -9.997277068014144/0.001596337468110117
getting coordinate (-1, 1)...
found 0 venues within 500 meters of -9.997277068014144/-0.001596337468110117
getting coordinate (1, -1)...
found 0 venues within 500 meters of -10.002722931985856/0.001596337468110117


{(-1, 0): Empty DataFrame
 Columns: []
 Index: [], (-1, 1): Empty DataFrame
 Columns: []
 Index: [], (0, -1): Empty DataFrame
 Columns: []
 Index: [], (0, 0): {}, (0, 1): Empty DataFrame
 Columns: []
 Index: [], (1, -1): Empty DataFrame
 Columns: []
 Index: [], (1, 0): Empty DataFrame
 Columns: []
 Index: []}

Works. We'll have to do some filtering later when looking for indicator venues, but that's later.

### Iterative search algorithm

The following iterative search will be performed:
1. Seed the venues_dict dictionary with the venues at the origin,
2. mark the origin as the first (and only) coordinate point not yet explored,
3. loop through exploring the coordinate point with the highest number of venues, until 100 coordinate points have been tested

In [82]:
def find_venues_geo_distribution(cities_df, city_index, max_coords_tested=100, radius=1500, limit=100, verbose=True):
    
    city_name = cities_df['City name'][city_index]
    city_state = cities_df['City state'][city_index]
    
    # initialize venues_dict with the venues dataframe at the origin
    venues_dict = {}
    origin_coord = (0,0)
    lat_orig = cities_df.Latitude[city_index]
    long_orig = cities_df.Longitude[city_index]
    print('[test #1 of {}] (0,0):'.format(max_coords_tested), end='')
    venues_df = getVenuesNearLatLong(lat_orig, long_orig, radius=radius, verbose=verbose)
    venues_dict[origin_coord] = venues_df
    
    # mark the origin as the first (and only) coordinate point not yet explored
    new_coords = [(0, 0)]
    num_coords_tested = 1
    
    while num_coords_tested < max_coords_tested:
        
        highest_venues = -1
        new_test_coord = None
        
        for this_coord in new_coords:
            venues_df = venues_dict[this_coord]
            if venues_df.shape[0] > highest_venues:
                new_test_coord = this_coord
                highest_venues = venues_df.shape[0]
        
        # call the hex grid exploration function
        num_coords_tested += 1
        print('[test #{} of {}]'.format(num_coords_tested, max_coords_tested), end=' ')
        new_coords = get_venues_in_hex_grid(lat_orig, long_orig, venues_dict, new_test_coord, radius=radius, new_coords=new_coords, limit=limit, verbose=verbose )
        
    return lat_orig, long_orig, venues_dict, city_name, city_state

### Test run on the first city

Manually test the algorithm for the first city in cities_df. The earlier fixed 10x10 grid needs to have overlap with this iteratively acquired geographic venues distribution.

In [83]:
lat_orig, long_orig, venues_dict, city_name, city_state = find_venues_geo_distribution(cities_df, 0, max_coords_tested=100, verbose=False)

[test #1 of 100] (0,0):55. [test #2 of 100] (-1,0):64. (1,0):69. (0,-1):93. (0,1):60. (-1,1):49. (1,-1):77. [test #3 of 100] (-1,-1):46. (0,-2):100. (1,-2):93. [test #4 of 100] (-1,-2):43. (0,-3):100. (1,-3):100. [test #5 of 100] (-1,-3):33. (0,-4):97. (1,-4):100. [test #6 of 100] (2,-3):100. (2,-4):100. [test #7 of 100] (1,-5):94. (2,-5):71. [test #8 of 100] (3,-3):96. (2,-2):100. (3,-4):75. [test #9 of 100] (3,-5):26. [test #10 of 100] (3,-2):75. (2,-1):58. [test #11 of 100] (-1,-4):24. (0,-5):11. [test #12 of 100] (4,-3):79. (4,-4):72. [test #13 of 100] (1,-6):41. (2,-6):72. [test #14 of 100] [test #15 of 100] (5,-3):27. (4,-2):45. (5,-4):23. [test #16 of 100] [test #17 of 100] (4,-5):18. [test #18 of 100] (3,-1):16. [test #19 of 100] (5,-5):18. [test #20 of 100] (3,-6):76. (2,-7):44. (3,-7):42. [test #21 of 100] (4,-6):27. (4,-7):24. [test #22 of 100] [test #23 of 100] (2,0):46. (1,1):57. [test #24 of 100] (-2,0):39. (-2,1):60. [test #25 of 100] (0,2):71. (-1,2):71. [test #26 of 10

In [84]:
make_map_from_dict(lat_orig, long_orig, venues_dict, 12, city_name, city_state, radius_zoom=0.2)

In [89]:
# test the second city in the list
lat_orig, long_orig, venues_dict, city_name, city_state = find_venues_geo_distribution(cities_df, 1, max_coords_tested=100, verbose=False)

[test #1 of 100] (0,0):5. [test #2 of 100] (-1,0):6. (1,0):4. (0,-1):9. (0,1):3. (-1,1):5. (1,-1):7. [test #3 of 100] (-1,-1):29. (0,-2):16. (1,-2):7. [test #4 of 100] (-2,-1):33. (-1,-2):31. (-2,0):22. [test #5 of 100] (-3,-1):34. (-2,-2):41. (-3,0):19. [test #6 of 100] (-3,-2):20. (-2,-3):23. (-1,-3):21. [test #7 of 100] (-4,-1):17. (-4,0):9. [test #8 of 100] (0,-3):9. [test #9 of 100] (-3,-3):19. (-2,-4):17. (-1,-4):13. [test #10 of 100] (-2,1):4. (-3,1):5. [test #11 of 100] (0,-4):9. [test #12 of 100] (-4,-2):23. [test #13 of 100] (-5,-2):18. (-4,-3):9. (-5,-1):7. [test #14 of 100] (-4,1):6. [test #15 of 100] (-3,-4):16. [test #16 of 100] (-6,-2):12. (-5,-3):17. (-6,-1):8. [test #17 of 100] (-5,0):8. [test #18 of 100] (-2,-5):9. (-1,-5):10. [test #19 of 100] (-6,-3):19. (-5,-4):19. (-4,-4):19. [test #20 of 100] (-7,-3):19. (-6,-4):27. (-7,-2):11. [test #21 of 100] (-7,-4):14. (-6,-5):36. (-5,-5):19. [test #22 of 100] (-7,-5):32. (-6,-6):31. (-5,-6):27. [test #23 of 100] (-8,-5):31.

In [90]:
make_map_from_dict(lat_orig, long_orig, venues_dict, 11, city_name, city_state, radius_zoom=0.2)

Looks like it's working ok. You can see clusters of venues and how they're spread out.

### Foursquare Personal Account

Because I'd really like to get more points at a better resolution (which also means not losing possible indicator venues that will go into the analysis later) I've upgraded to the Foursquare personal account. Now armed with 99,500 queries per day, Let's look at the same two cities from above but now with 800 meter resolution and 1000 query points.



In [85]:
lat_orig, long_orig, venues_dict, city_name, city_state = find_venues_geo_distribution(cities_df, 0, radius=800, max_coords_tested=1000, verbose=False)

[test #1 of 1000] (0,0):24. [test #2 of 1000] (-1,0):15. (1,0):23. (0,-1):20. (0,1):37. (-1,1):26. (1,-1):21. [test #3 of 1000] (1,1):38. (0,2):31. (-1,2):25. [test #4 of 1000] (2,1):23. (1,2):33. (2,0):15. [test #5 of 1000] (2,2):18. (1,3):24. (0,3):24. [test #6 of 1000] (-1,3):16. [test #7 of 1000] (-2,1):28. (-2,2):29. [test #8 of 1000] (-3,2):22. (-2,3):9. (-3,3):19. [test #9 of 1000] (-3,1):26. (-2,0):4. [test #10 of 1000] (-4,1):27. (-3,0):4. (-4,2):33. [test #11 of 1000] (-5,2):31. (-4,3):22. (-5,3):25. [test #12 of 1000] (-6,2):29. (-5,1):30. (-6,3):27. [test #13 of 1000] (-6,1):24. (-5,0):7. (-4,0):6. [test #14 of 1000] (-7,2):19. (-7,3):12. [test #15 of 1000] [test #16 of 1000] (-6,4):39. (-7,4):28. [test #17 of 1000] (-5,4):25. (-6,5):40. (-7,5):41. [test #18 of 1000] (-8,5):17. (-7,6):43. (-8,6):24. [test #19 of 1000] (-6,6):25. (-7,7):16. (-8,7):18. [test #20 of 1000] (-5,5):18. [test #21 of 1000] (-8,4):13. [test #22 of 1000] [test #23 of 1000] [test #24 of 1000] (-4,4):1

7. (-10,9):7. [test #215 of 1000] (-9,5):4. [test #216 of 1000] [test #217 of 1000] (6,13):7. [test #218 of 1000] (3,6):5. [test #219 of 1000] (-6,16):4. (-7,16):6. [test #220 of 1000] (8,5):6. (7,5):5. [test #221 of 1000] (13,3):14. (12,4):4. [test #222 of 1000] (-8,15):4. (-8,16):5. [test #223 of 1000] (-2,-5):14. [test #224 of 1000] [test #225 of 1000] (8,-8):2. [test #226 of 1000] (-3,20):2. (-4,21):5. (-5,21):5. [test #227 of 1000] (-6,21):5. [test #228 of 1000] (11,-7):2. (10,-6):9. (11,-8):6. [test #229 of 1000] (-8,10):3. (-9,10):5. [test #230 of 1000] [test #231 of 1000] [test #232 of 1000] [test #233 of 1000] (3,-1):7. [test #234 of 1000] (6,8):13. [test #235 of 1000] (-1,-7):8. (0,-8):4. [test #236 of 1000] [test #237 of 1000] (-2,18):10. [test #238 of 1000] (-10,10):6. [test #239 of 1000] [test #240 of 1000] [test #241 of 1000] (-1,17):11. [test #242 of 1000] [test #243 of 1000] (12,-1):13. [test #244 of 1000] (4,17):2. (3,18):6. (2,18):31. [test #245 of 1000] (1,18):26. (2

15. [test #453 of 1000] (6,-25):4. (7,-26):5. [test #454 of 1000] [test #455 of 1000] (15,-28):5. (15,-29):11. [test #456 of 1000] (13,-30):24. (14,-30):17. [test #457 of 1000] (12,-30):15. (13,-31):22. (14,-31):14. [test #458 of 1000] (15,-30):12. [test #459 of 1000] (12,-31):12. (13,-32):12. (14,-32):24. [test #460 of 1000] (15,-32):12. (14,-33):7. (15,-33):2. [test #461 of 1000] (9,-22):14. [test #462 of 1000] (8,-27):6. [test #463 of 1000] (10,-23):4. [test #464 of 1000] (10,-28):7. [test #465 of 1000] (15,-31):10. [test #466 of 1000] (15,-27):1. (14,-26):4. [test #467 of 1000] (11,-30):5. (11,-29):4. [test #468 of 1000] [test #469 of 1000] (13,-25):3. [test #470 of 1000] [test #471 of 1000] (10,-22):1. [test #472 of 1000] [test #473 of 1000] (16,-30):15. (16,-31):11. [test #474 of 1000] (17,-30):11. (16,-29):16. (17,-31):8. [test #475 of 1000] (17,-29):7. (16,-28):5. [test #476 of 1000] (11,-31):1. (12,-32):10. [test #477 of 1000] (13,-33):5. [test #478 of 1000] (16,-32):8. (16,-3

5. (15,-14):4. [test #666 of 1000] [test #667 of 1000] (-9,0):7. [test #668 of 1000] (-11,-1):5. (-10,-1):6. [test #669 of 1000] (-5,-7):6. (-6,-7):5. [test #670 of 1000] (19,6):5. (18,7):2. (17,7):5. [test #671 of 1000] (19,-4):5. [test #672 of 1000] [test #673 of 1000] (-8,0):5. (-9,-1):5. (-8,-1):5. [test #674 of 1000] (-3,-1):4. [test #675 of 1000] [test #676 of 1000] [test #677 of 1000] [test #678 of 1000] [test #679 of 1000] [test #680 of 1000] [test #681 of 1000] [test #682 of 1000] [test #683 of 1000] [test #684 of 1000] [test #685 of 1000] (3,-14):5. [test #686 of 1000] (-3,-2):4. [test #687 of 1000] [test #688 of 1000] (14,-1):5. [test #689 of 1000] (-7,17):3. (-8,17):6. [test #690 of 1000] [test #691 of 1000] [test #692 of 1000] (-10,11):4. (-11,11):8. [test #693 of 1000] (-12,11):5. (-11,12):8. (-12,12):7. [test #694 of 1000] (-11,13):12. (-12,13):11. [test #695 of 1000] (-11,14):5. (-12,14):13. [test #696 of 1000] (-13,14):19. (-12,15):5. (-13,15):7. [test #697 of 1000] (-

4. [test #888 of 1000] (-12,-5):0. [test #889 of 1000] (-7,-8):4. [test #890 of 1000] [test #891 of 1000] (-7,-9):6. [test #892 of 1000] [test #893 of 1000] (-12,-2):5. [test #894 of 1000] (-12,-8):4. (-11,-9):5. [test #895 of 1000] [test #896 of 1000] [test #897 of 1000] (-10,-10):5. [test #898 of 1000] (-12,-1):6. [test #899 of 1000] (-5,-5):4. (-6,-5):4. [test #900 of 1000] (14,6):3. [test #901 of 1000] (10,11):3. [test #902 of 1000] [test #903 of 1000] [test #904 of 1000] [test #905 of 1000] (17,14):7. [test #906 of 1000] (18,14):2. [test #907 of 1000] (6,17):4. (7,18):4. (6,18):4. [test #908 of 1000] [test #909 of 1000] (15,18):0. [test #910 of 1000] [test #911 of 1000] (10,17):3. (9,17):5. [test #912 of 1000] (-13,-7):9. (-13,-6):5. [test #913 of 1000] (-14,-7):9. (-13,-8):7. (-14,-6):7. [test #914 of 1000] (-15,-7):8. (-14,-8):9. (-15,-6):7. [test #915 of 1000] (-15,-8):11. (-14,-9):9. (-13,-9):5. [test #916 of 1000] (-16,-8):14. (-15,-9):9. (-16,-7):11. [test #917 of 1000] (-17

In [88]:
make_map_from_dict(lat_orig, long_orig, venues_dict, 11, city_name, city_state, radius_zoom=0.2)

In [102]:
lat_orig, long_orig, venues_dict, city_name, city_state = find_venues_geo_distribution(cities_df, 1, radius=800, max_coords_tested=1000, verbose=False)

[test #1 of 1000] (0,0):2. [test #2 of 1000] (-1,0):4. (1,0):3. (0,-1):3. (0,1):4. (-1,1):3. (1,-1):3. [test #3 of 1000] (-2,0):4. (-1,-1):3. (-2,1):3. [test #4 of 1000] (1,1):2. (0,2):1. (-1,2):2. [test #5 of 1000] (-3,0):6. (-2,-1):5. (-3,1):2. [test #6 of 1000] (-4,0):7. (-3,-1):12. (-4,1):3. [test #7 of 1000] (-4,-1):19. (-3,-2):26. (-2,-2):18. [test #8 of 1000] (-4,-2):22. (-3,-3):23. (-2,-3):23. [test #9 of 1000] (-4,-3):11. (-3,-4):4. (-2,-4):12. [test #10 of 1000] (-1,-3):10. (-1,-4):10. [test #11 of 1000] (-5,-2):16. (-5,-1):17. [test #12 of 1000] (-5,0):10. [test #13 of 1000] (-1,-2):4. [test #14 of 1000] (-6,-1):4. (-6,0):4. [test #15 of 1000] (-6,-2):8. (-5,-3):10. [test #16 of 1000] (-2,-5):4. (-1,-5):5. [test #17 of 1000] (-4,-4):17. [test #18 of 1000] (-5,-4):15. (-4,-5):14. (-3,-5):10. [test #19 of 1000] (-6,-4):10. (-5,-5):13. (-6,-3):11. [test #20 of 1000] (-4,-6):7. (-3,-6):11. [test #21 of 1000] (-6,-5):2. (-5,-6):4. [test #22 of 1000] (-7,-3):4. (-7,-2):8. [test #2

37. [test #192 of 1000] (-8,-30):25. [test #193 of 1000] (-8,-22):35. [test #194 of 1000] (-11,-32):6. (-10,-32):12. [test #195 of 1000] (-10,-18):22. [test #196 of 1000] (-15,-23):31. [test #197 of 1000] (-18,-31):28. (-17,-32):16. (-18,-30):44. [test #198 of 1000] [test #199 of 1000] (-16,-28):57. (-15,-27):54. (-16,-27):50. [test #200 of 1000] (-17,-28):24. (-17,-27):39. [test #201 of 1000] (-14,-27):35. (-15,-26):33. (-16,-26):55. [test #202 of 1000] (-17,-26):48. (-16,-25):37. (-17,-25):29. [test #203 of 1000] [test #204 of 1000] (-7,-21):46. (-7,-22):29. [test #205 of 1000] (-18,-26):36. (-18,-25):19. [test #206 of 1000] [test #207 of 1000] [test #208 of 1000] (-6,-21):24. (-7,-20):27. (-6,-22):21. [test #209 of 1000] [test #210 of 1000] (-14,-33):10. (-13,-33):2. [test #211 of 1000] (-12,-33):3. [test #212 of 1000] (-12,-17):17. (-13,-17):17. [test #213 of 1000] (-8,-19):16. [test #214 of 1000] (-19,-30):31. (-18,-29):27. (-19,-29):30. [test #215 of 1000] [test #216 of 1000] (-2

6. (-13,-16):14. [test #423 of 1000] [test #424 of 1000] [test #425 of 1000] [test #426 of 1000] (-21,-12):16. (-22,-12):28. [test #427 of 1000] (-23,-12):31. (-22,-11):12. (-23,-11):31. [test #428 of 1000] (-24,-12):26. (-23,-13):6. (-24,-11):29. [test #429 of 1000] (-23,-10):11. (-24,-10):32. [test #430 of 1000] (-25,-10):27. (-24,-9):6. (-25,-9):6. [test #431 of 1000] (-25,-11):31. [test #432 of 1000] (-26,-11):16. (-25,-12):14. (-26,-10):15. [test #433 of 1000] (-26,-9):16. [test #434 of 1000] (-24,-13):8. [test #435 of 1000] (-5,-20):7. (-6,-19):9. [test #436 of 1000] [test #437 of 1000] [test #438 of 1000] (-6,-29):10. [test #439 of 1000] (0,-31):9. (0,-32):8. [test #440 of 1000] (1,-32):17. [test #441 of 1000] (2,-32):25. (1,-31):34. [test #442 of 1000] (2,-31):30. (1,-30):35. (0,-30):24. [test #443 of 1000] (2,-30):27. (1,-29):28. (0,-29):28. [test #444 of 1000] (3,-31):20. (3,-32):15. [test #445 of 1000] (2,-29):15. (1,-28):7. (0,-28):7. [test #446 of 1000] (-1,-29):23. (-1,-2

21. (-38,-19):18. [test #614 of 1000] (-38,-21):20. (-37,-22):17. [test #615 of 1000] (-31,-25):15. (-30,-25):15. [test #616 of 1000] (-37,-18):32. (-38,-18):29. [test #617 of 1000] (-36,-18):15. (-37,-17):26. (-38,-17):23. [test #618 of 1000] (-39,-18):18. (-39,-17):30. [test #619 of 1000] (-40,-17):13. (-39,-16):23. (-40,-16):17. [test #620 of 1000] (-36,-17):16. (-37,-16):10. (-38,-16):14. [test #621 of 1000] [test #622 of 1000] (-39,-15):7. (-40,-15):12. [test #623 of 1000] (-29,-22):30. (-30,-21):23. (-29,-23):10. [test #624 of 1000] (-28,-22):24. (-29,-21):28. (-28,-23):9. [test #625 of 1000] (-28,-21):25. (-29,-20):15. [test #626 of 1000] (-27,-21):14. (-27,-22):13. [test #627 of 1000] (-27,-23):5. [test #628 of 1000] [test #629 of 1000] (-35,-17):16. (-35,-16):16. [test #630 of 1000] [test #631 of 1000] (-33,-24):10. (-32,-25):24. [test #632 of 1000] (-33,-25):10. (-32,-26):29. (-31,-26):27. [test #633 of 1000] (-33,-26):22. (-32,-27):22. (-31,-27):21. [test #634 of 1000] (-30,

6. [test #854 of 1000] [test #855 of 1000] [test #856 of 1000] [test #857 of 1000] (-45,-8):6. (-46,-7):7. [test #858 of 1000] (-44,-6):6. [test #859 of 1000] [test #860 of 1000] [test #861 of 1000] (-28,-24):5. [test #862 of 1000] [test #863 of 1000] [test #864 of 1000] (-32,-29):2. [test #865 of 1000] [test #866 of 1000] (-34,-28):6. [test #867 of 1000] [test #868 of 1000] (-51,-2):9. (-52,-2):11. [test #869 of 1000] (-53,-2):1. (-52,-1):3. (-53,-1):0. [test #870 of 1000] (-3,-21):9. (-4,-20):10. (-3,-22):7. [test #871 of 1000] (3,-28):7. (2,-27):9. (1,-27):8. [test #872 of 1000] (-30,-9):7. [test #873 of 1000] [test #874 of 1000] (-51,-15):6. (-51,-14):5. [test #875 of 1000] [test #876 of 1000] (-3,-20):6. (-4,-19):2. (-5,-19):5. [test #877 of 1000] (-21,-6):5. (-21,-5):7. [test #878 of 1000] (-15,-8):4. [test #879 of 1000] [test #880 of 1000] [test #881 of 1000] [test #882 of 1000] [test #883 of 1000] (-5,-27):4. (-6,-27):8. [test #884 of 1000] [test #885 of 1000] (-6,-18):2. [test

In [103]:
make_map_from_dict(lat_orig, long_orig, venues_dict, 11, city_name, city_state, radius_zoom=0.2)

This looks much nicer. The queries rarely hit the limit of 100 venues, which means there's little chance that indicator venues would be missed.

### Determine aggregates describing the geographical distribution

In order to cluster cities by shape of their venues, we need to calculate aggregate variables:
* Determine the center of the venues by averaging each coordinate point, weighed by the number of venues there.
* Determine the mean distance of all venues from that center.
* Determine the standard deviation of the distance distribution, as well as skewedness and kurtosis ("peaky-ness").
Once we have these values, all details on the geographic venues distribution will be discarded.

(We will sum up the number of indicator venues as compared to the total number of venues as well, but that's not geographic information.)